# Music Transfomers

## Importing libraries

It's necessary to modify the file `gym_utils` in the original `tensor2tensor` package in order to make it work with music transformers.
This is the PR related to the necessary changes
https://github.com/tensorflow/tensor2tensor/pull/1908/files

Check the **Setting up the environment** section in the [README](../README.md)  for more details on how to do that.

If you are running the environment on docker you don't need to worry about that, this dependency adjustment is for local deployment only

In [1]:
import warnings
warnings.filterwarnings('ignore')  # Comment to show warnings, can be useful for troubleshooting

import datetime
import shutil
import numpy as np
import tensorflow.compat.v1 as tf

from tensor2tensor.data_generators import text_encoder
from tensor2tensor.utils import decoding
from tensor2tensor.utils import trainer_lib

from magenta.models.score2perf import score2perf
import note_seq

tf.logging.set_verbosity(tf.logging.ERROR) # Comment to show logging info, can be useful for troubleshooting
tf.disable_v2_behavior()


print('Importing libraries done!')

Importing libraries done!


## Global variables and helper functions definition

In [2]:
MODEL_NAME = 'transformer' # name of the model
HPARAMS_SET = 'transformer_tpu' # hyper-parameters set
UNCONDITIONAL_CKPT_PATH = '../bin/checkpoints/unconditional_model_16.ckpt' # choosen checkpoint of model weights for unconditional generation
MELODY_MODEL_CKPT_PATH = '../bin/checkpoints/melody_conditioned_model_16.ckpt' # choosen checkpoint of model weights for melody-acc generation

# Soundfont path and sample rate for midi output
SF2_PATH = '../bin/soundfont/Yamaha-C5-Salamander-JNv5.1.sf2' 
SAMPLE_RATE = 16000 

# Define model classes
class PianoPerformanceLanguageModelProblem(score2perf.Score2PerfProblem):
    @property
    def add_eos_symbol(self):
        return True

class MelodyToPianoPerformanceProblem(score2perf.AbsoluteMelody2PerfProblem):
  @property
  def add_eos_symbol(self):
    return True

# Define helper functions

# Create input generator for unconditional model
def input_generator(targets, decode_length):
    while True:
        yield {
            'targets': np.array([targets], dtype=np.int32),
            'decode_length': np.array(decode_length, dtype=np.int32)
        }

# Create input generator for Melody model.
def melody_input_generator(inputs, decode_length):
    while True:
        yield {
            'inputs': np.array([[inputs]], dtype=np.int32),
            'targets': np.zeros([1, 0], dtype=np.int32),
            'decode_length': np.array(decode_length, dtype=np.int32)
        }


# Decode a list of IDs.
def decode(ids, encoder):
    ids = list(ids)
    if text_encoder.EOS_ID in ids:
        ids = ids[:ids.index(text_encoder.EOS_ID)]
    return encoder.decode(ids)


# Creates model estimator
def create_estimator(model):
    # Set up Hyper-parameters definition.
    hparams = trainer_lib.create_hparams(hparams_set=HPARAMS_SET)
    hparams.num_hidden_layers = 16
    hparams.sampling_method = 'random'

    trainer_lib.add_problem_hparams(hparams, model)

    # Set up decoder HParams.
    decode_hparams = decoding.decode_hparams()
    decode_hparams.alpha = 0.0
    decode_hparams.beam_size = 1

    # Create Estimator.
    run_config = trainer_lib.create_run_config(hparams)
    estimator = trainer_lib.create_estimator(
        MODEL_NAME,
        hparams,
        run_config,
        decode_hparams=decode_hparams)
    return estimator


# Map sequence to Melody model input
def map_melody_to_input_tokens(melody):
    # Tokens to insert between melody events. (continuation of note)
    event_padding = 2 * [note_seq.MELODY_NO_EVENT]

    events = list()
    for e in melody:
        for event in [e] + event_padding:
            processed_event = event + 12 if event != note_seq.MELODY_NO_EVENT else event
            events.append(processed_event)
    events_str = ' '.join(str(e) for e in events)
    return events_str

## Unconditional generation

Unconditional generation can also be interpreted as "generate a piano performance from scratch".
This can take a minute or so depending on the length of the performance the model ends up generating.

Due to the chosen [representation](http://g.co/magenta/performance-rnn) where each event corresponds to 
a variable amount of time, the actual number of seconds generated may vary.

In [ ]:
# Defines model type and conditional encoders
model = PianoPerformanceLanguageModelProblem()
unconditional_encoders = model.get_feature_encoders()

# Start the Estimator with the input function for the model, loading from the specified checkpoint.
estimator = create_estimator(model)

# Defines input generator function. The targets are set as an empty array as it's a completely unconditional generation.
# The decode_length is set to 1024 tokens, meaning that this amount of musical events will be generated.
generator_function = input_generator(targets=[], decode_length=1024)
input_fn = decoding.make_input_fn_from_generator(generator_function)
unconditional_samples = estimator.predict(input_fn, checkpoint_path=UNCONDITIONAL_CKPT_PATH)

# "Burn" one in order to ignore the first "piece_start" token.
_ = next(unconditional_samples)

# Generate sample events.
sample_ids = next(unconditional_samples)['outputs']

# Decode sample ids to NoteSequence.
unconditional_generated_midi = decode(sample_ids, encoder=unconditional_encoders['targets'])
unconditional_ns = note_seq.midi_file_to_note_sequence(unconditional_generated_midi)

In [ ]:
## Play and plot unconditional generated excerpt

In [4]:
note_seq.play_sequence(
    unconditional_ns,
    synth=note_seq.fluidsynth,
    sample_rate=SAMPLE_RATE,
    sf2_path=SF2_PATH)

note_seq.plot_sequence(unconditional_ns)

# Saves generated sequence in midi format
note_seq.sequence_proto_to_midi_file(unconditional_ns, 'unconditional.mid')

fluidsynth: error: Unknown integer parameter 'synth.sample-rate'


Loading BokehJS ...

## Conditional generation

This type of generation can be seem as asking the model to "continue the music". In this type of task, we give to the model a primer excerpt so it can continue from there.
You can find examples of model excerpts at the [primers](../primers) folder, and you can also add any primer you want as long as it's in the MIDI format

In [ ]:
PRIMERS_LOCATION_PATH = '../primers/'

filenames = {
    'C major arpeggio': PRIMERS_LOCATION_PATH + 'c_major_arpeggio.mid',
    'C major scale': PRIMERS_LOCATION_PATH + 'c_major_scale.mid',
    'Clair de Lune': PRIMERS_LOCATION_PATH + 'clair_de_lune.mid',
    'Fur elise': PRIMERS_LOCATION_PATH + 'fur_elise.mid',
    'Moonlight sonata': PRIMERS_LOCATION_PATH + 'moonlight_sonata.mid',
    'Prelude in C major': PRIMERS_LOCATION_PATH + 'prelude_in_c_major.mid'
}


PRIMER_MIDI_FILE = filenames['Moonlight sonata']

# Extract note-sequence from midi file
primer_ns = note_seq.midi_file_to_note_sequence(PRIMER_MIDI_FILE)

# Defines model type and conditional encoders
model = PianoPerformanceLanguageModelProblem()
conditional_encoders = model.get_feature_encoders()
estimator = create_estimator(model)

# Encode primer note sequence as target for the model
primer_targets = conditional_encoders['targets'].encode_note_sequence(primer_ns)

# Remove the end ("piece_end") token from the encoded primer.
primer_targets = primer_targets[:-1]

 # decode length of melody generation considering primer size
decode_length = max(0, 4096 - len(primer_targets))

# Create input generator
generator_fn = input_generator(primer_targets, decode_length)
conditional_input_fn = decoding.make_input_fn_from_generator(generator_fn)

conditional_samples = estimator.predict(conditional_input_fn, checkpoint_path=UNCONDITIONAL_CKPT_PATH)

# "Burn" one in order to ignore the first "piece_start" token.
_ = next(conditional_samples)
sample_ids = next(conditional_samples)['outputs']


conditional_generated_midi = decode(sample_ids, encoder=conditional_encoders['targets'])
conditional_sequence = note_seq.midi_file_to_note_sequence(conditional_generated_midi)

# Merge primer with its generated continuation
full_sequence_ns = note_seq.concatenate_sequences([primer_ns, conditional_sequence])

## Play and plot conditional generated excerpt

In [6]:
# Play and plot.
note_seq.play_sequence(
    full_sequence_ns,
    synth=note_seq.fluidsynth,
    sample_rate=SAMPLE_RATE,
    sf2_path=SF2_PATH)

note_seq.plot_sequence(full_sequence_ns)
note_seq.sequence_proto_to_midi_file(full_sequence_ns, 'continuation.mid')

fluidsynth: error: Unknown integer parameter 'synth.sample-rate'


Loading BokehJS ...

## Generate melody accompaniment

In this task, the model generates the harmony around a given melody. 
To exemplify in a different way, let's create the melodies manually, instead of using a MIDI primer file as we did in the example before.
In this approach, we create the MIDI events manually into an array

In [7]:
melodies = {
    'Mary Had a Little Lamb': [
        64, 62, 60, 62, 64, 64, 64, note_seq.MELODY_NO_EVENT,
        62, 62, 62, note_seq.MELODY_NO_EVENT,
        64, 67, 67, note_seq.MELODY_NO_EVENT,
        64, 62, 60, 62, 64, 64, 64, 64,
        62, 62, 64, 62, 60, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT
    ],
    'Row Row Row Your Boat': [
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        60, note_seq.MELODY_NO_EVENT, 62,
        64, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        64, note_seq.MELODY_NO_EVENT, 62,
        64, note_seq.MELODY_NO_EVENT, 65,
        67, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        72, 72, 72, 67, 67, 67, 64, 64, 64, 60, 60, 60,
        67, note_seq.MELODY_NO_EVENT, 65,
        64, note_seq.MELODY_NO_EVENT, 62,
        60, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT,
        note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT, note_seq.MELODY_NO_EVENT
    ],
    'Twinkle Twinkle Little Star': [
        60, 60, 67, 67, 69, 69, 67, note_seq.MELODY_NO_EVENT,
        65, 65, 64, 64, 62, 62, 60, note_seq.MELODY_NO_EVENT,
        67, 67, 65, 65, 64, 64, 62, note_seq.MELODY_NO_EVENT,
        67, 67, 65, 65, 64, 64, 62, note_seq.MELODY_NO_EVENT,
        60, 60, 67, 67, 69, 69, 67, note_seq.MELODY_NO_EVENT,
        65, 65, 64, 64, 62, 62, 60, note_seq.MELODY_NO_EVENT
    ]
}

melody = 'Row Row Row Your Boat'
primer_melody_tokens = map_melody_to_input_tokens(melodies[melody])

In [ ]:
# Defines model type and encoders
model = MelodyToPianoPerformanceProblem()
melody_encoders = model.get_feature_encoders()
estimator = create_estimator(model)

# Encode primer melody tokens as input for the model
encoded_inputs = melody_encoders['inputs'].encode(primer_melody_tokens)

# Create input generator
generator_function = melody_input_generator(inputs=encoded_inputs, decode_length=4096)
input_fn = decoding.make_input_fn_from_generator(generator_function)


# Predict samples
samples = estimator.predict(input_fn, checkpoint_path=MELODY_MODEL_CKPT_PATH)

# "Burn" one in order to ignore the first "piece_start" token.
_ = next(samples)

# Generate sample events.
sample_ids = next(samples)['outputs']

melody_accompaniment_midi = decode(sample_ids, encoder=melody_encoders['targets'])
melody_accompaniment_ns = note_seq.midi_file_to_note_sequence(melody_accompaniment_midi)

## Play and plot melody excerpt

In [9]:
note_seq.play_sequence(
    melody_accompaniment_ns,
    synth=note_seq.fluidsynth,
    sample_rate=SAMPLE_RATE,
    sf2_path=SF2_PATH)

note_seq.plot_sequence(melody_accompaniment_ns)

# Saves generated sequence in midi format
note_seq.sequence_proto_to_midi_file(melody_accompaniment_ns, 'melody_accompaniment.mid')

fluidsynth: error: Unknown integer parameter 'synth.sample-rate'


Loading BokehJS ...